# Amazon Redshift Serverless monitoring System views

# How to monitor queries based on status?
Use SYS_QUERY_HISTORY to view details of user queries. Each row represents a user query with accumulated statistics for some of the fields. This view contains many types of queries, such as data definition language (DDL), data manipulation language (DML), copy, unload, and Amazon Redshift Spectrum. It contains both running and finished queries.

https://docs.aws.amazon.com/redshift/latest/dg/SYS_QUERY_HISTORY.html

*All time metrics are in microseconds*

In [0]:
SELECT user_id,
       query_id,
       transaction_id,
       session_id,
       status,
       trim(database_name) AS database_name,
       start_time,
       end_time,
       result_cache_hit,
       elapsed_time as elapsed_time_InMicroseconds,
       queue_time as queue_time_InMicroseconds,
       execution_time as execution_time_InMicroseconds
FROM sys_query_history
ORDER BY start_time;

# How to monitor individual query elaspsed time breakdown details?
The following query returns the query start time, end time, queue time, elapsed time, planning time, and other metadata for a specific query
replace <query_id>


https://docs.aws.amazon.com/redshift/latest/dg/SYS_QUERY_HISTORY.html

*All time metrics are in microseconds*

In [0]:
SELECT user_id,
       query_id,
       transaction_id,
       session_id,
       status,
       trim(database_name) AS database_name,
       start_time,
       end_time,
       result_cache_hit,
       lock_wait_time,
       compile_time,
       planning_time,
       elapsed_time,
       queue_time,
       execution_time,
       planning_time,
       trim(query_text) as query_text
FROM sys_query_history
WHERE query_id = <query_id>;

# How to monitor workload breakdown by query count, and percentile run time?

https://docs.aws.amazon.com/redshift/latest/dg/SYS_QUERY_HISTORY.html

In [0]:
WITH queries AS
(
  select
  date_trunc('hour', q.start_time) as "period"
  ,q.query_type
  ,q.elapsed_time / 1000000.00 as "total_elapsed_s" 
  FROM sys_query_history q
  WHERE q.user_id > 1
  AND   q.status != 'failed'
)
  SELECT period,
         query_type,
         COUNT(*) AS query_count,
         ROUND(PERCENTILE_CONT (0.25) WITHIN GROUP(ORDER BY total_elapsed_s),2) AS p25_s,
         ROUND(PERCENTILE_CONT (0.50) WITHIN GROUP(ORDER BY total_elapsed_s),2) AS p50_s,
         ROUND(PERCENTILE_CONT (0.75) WITHIN GROUP(ORDER BY total_elapsed_s),2) AS p75_s,
         ROUND(PERCENTILE_CONT (0.90) WITHIN GROUP(ORDER BY total_elapsed_s),2) AS p90_s,
         ROUND(PERCENTILE_CONT (0.95) WITHIN GROUP(ORDER BY total_elapsed_s),2) AS p95_s,
         ROUND(PERCENTILE_CONT (0.99) WITHIN GROUP(ORDER BY total_elapsed_s),2) AS p99_s,
         MAX(total_elapsed_s) AS max_s,
         AVG(total_elapsed_s) AS avg_s,
         stddev(total_elapsed_s) AS std_s
  FROM queries
  GROUP BY 1,2
  order by 1;

# How to monitor detailed steps involved in query execution?
## The following query shows the query metadata detail at step level, including step name, input_bytes, output_bytes, input_rows, output_rows
 replace <query_id>

 https://docs.aws.amazon.com/redshift/latest/dg/SYS_QUERY_DETAIL.html

In [0]:
SELECT query_id,
       child_query_sequence,
       stream_id,
       segment_id,
       step_id,
       trim(step_name) AS step_name,
       duration,
       input_bytes,
       output_bytes,
       input_rows,
       output_rows
FROM sys_query_detail
WHERE query_id = <query_id>
ORDER BY query_id,
         stream_id,
         segment_id,
         step_id DESC;

# How to monitor serverless usage cost by day?

https://docs.aws.amazon.com/redshift/latest/dg/SYS_SERVERLESS_USAGE.html

## update the <Price for 1 RPU> based on your region refer to Amazon Redshift pricing page

https://aws.amazon.com/redshift/pricing/?refid=765e8455-cae6-4207-a6bc-c454bfc2c9d8#Amazon_Redshift_Serverless

In [0]:
select trunc(start_time) "Day", 
(sum(charged_seconds)/3600::double precision) * <Price for 1 RPU> as cost_incurred 
from sys_serverless_usage 
group by 1 
order by 1;

# How to monitor copy command?
## Query to show the loaded rows, bytes, tables and data source of copy commands

https://docs.aws.amazon.com/redshift/latest/dg/SYS_LOAD_HISTORY.html

In [0]:
SELECT query_id,
       table_name,
       data_source,
       loaded_rows,
       loaded_bytes
FROM sys_load_history
ORDER BY query_id DESC;

# How to monitor for number of sessions, and connections? 
## To view the details for open connections, run the following query.

https://docs.aws.amazon.com/redshift/latest/dg/SYS_CONNECTION_LOG.html

In [0]:
select trim(event) as event, count(*)
from sys_connection_log
where trim(event) = 'initiating session'
and user_name not in ('rdsdb')
and (session_id,database_name,remote_host,remote_port,user_name) not in 
(select session_id,database_name,remote_host,remote_port,user_name from sys_connection_log
where trim(event) = 'disconnecting session')
group by 1
order by 1 desc;

# How to monitor Data Ingestion metrics?

In [0]:
SELECT  
  date_trunc('hour', start_time) period_hourly
  , database_name
  , table_name
  , status
  , file_format
  , SUM(loaded_rows) total_rows_ingested
  , SUM(loaded_bytes) total_bytes_ingested
  , SUM(source_file_count) num_of_files_to_process
  , SUM(file_count_scanned) num_of_files_processed
  , SUM(error_count) total_errors
FROM    
  sys_load_history
GROUP BY
  period_hourly
  , database_name
  , table_name
  , status
  , file_format
ORDER BY
  table_name
  , period_hourly
  , status;

# How to monitor external queries such as queries run against data in S3 (Spectrum quries)?

Reference: https://docs.aws.amazon.com/redshift/latest/dg/SYS_EXTERNAL_QUERY_DETAIL.html

In [0]:
SELECT  
  DATE_TRUNC('hour', start_time) period_hourly
  , user_id
  , TRIM(source_type) source_type
  , COUNT (DISTINCT query_id) query_counts
  , SUM(returned_rows) returned_rows
  , ROUND(SUM(returned_bytes) / 1024^3,2) returned_gb
FROM    
  sys_external_query_detail
GROUP BY
  period_hourly
  , user_id
  , source_type
ORDER BY
  period_hourly
  , user_id
  , source_type;

# How to find top 100 long running queries?

In [0]:
SELECT  
  user_id
  , transaction_id
  , query_id
  , database_name
  , query_type
  , query_text::VARCHAR(100)
  , lock_wait_time
  , planning_time
  , compile_time
  , execution_time
  , elapsed_time
FROM    
  sys_query_history
ORDER BY
  elapsed_time DESC
LIMIT 100;